In [1]:
import pandas as pd
import numpy as np

from datetime import datetime
from pandas_datareader import data

import pandas_datareader
import bs4 as bs
import pickle
import requests

<h2>Downloading of data</h2>

In [31]:
def save_sp500_tickers():
    resp = requests.get('http://en.wikipedia.org/wiki/List_of_S%26P_500_companies')
    soup = bs.BeautifulSoup(resp.text, 'lxml')
    table = soup.find('table', {'class': 'wikitable sortable'})
    tickers = []
    for row in table.findAll('tr')[1:]:
        ticker = row.findAll('td')[0].text
        tickers.append(ticker)
        
    with open("sp500tickers.pickle","wb") as f:
        pickle.dump(tickers,f)
        
    return tickers

tickerList = save_sp500_tickers()
tickerList = [ticker[:-1] for ticker in tickerList]
tickerList = [ticker.replace('.', '-') for ticker in tickerList]
tickerList.append('^GSPC')

In [32]:
def get_stocks_data(ticker, source):
    Ticker = pandas_datareader.data.DataReader(ticker, source)
    Ticker['Ticker'] = ticker
    return Ticker
    
stocks_data = [get_stocks_data(ticker, 'yahoo') for ticker in tickerList]

In [33]:
stocks_data

[                  High         Low        Open       Close      Volume  \
 Date                                                                     
 2010-01-04   83.449997   82.669998   83.089996   83.019997   3043700.0   
 2010-01-05   83.230003   81.699997   82.800003   82.500000   2847000.0   
 2010-01-06   84.599998   83.510002   83.879997   83.669998   5268500.0   
 2010-01-07   83.760002   82.120003   83.320000   83.730003   4470100.0   
 2010-01-08   84.320000   83.300003   83.690002   84.320000   3405800.0   
 2010-01-11   84.599998   83.410004   84.379997   83.980003   2927100.0   
 2010-01-12   84.180000   83.300003   83.580002   84.050003   3031800.0   
 2010-01-13   84.110001   83.199997   84.110001   83.779999   3102000.0   
 2010-01-14   83.930000   83.419998   83.739998   83.500000   2634100.0   
 2010-01-15   84.089996   82.870003   83.519997   83.370003   3955000.0   
 2010-01-19   85.169998   83.500000   83.820000   85.120003   4500400.0   
 2010-01-20   85.129997  

In [25]:
'''stocks_data = pd.concat(stocks_data, axis=0)
stocks_data = stocks_data.set_index(['Ticker'], append=True)
stocks_data.head()'''

High        Low       Open      Close     Volume  \
Date       Ticker                                                          
2010-01-04 MMM     83.449997  82.669998  83.089996  83.019997  3043700.0   
2010-01-05 MMM     83.230003  81.699997  82.800003  82.500000  2847000.0   
2010-01-06 MMM     84.599998  83.510002  83.879997  83.669998  5268500.0   
2010-01-07 MMM     83.760002  82.120003  83.320000  83.730003  4470100.0   
2010-01-08 MMM     84.320000  83.300003  83.690002  84.320000  3405800.0   

                   Adj Close  
Date       Ticker             
2010-01-04 MMM     65.798973  
2010-01-05 MMM     65.386833  
2010-01-06 MMM     66.314133  
2010-01-07 MMM     66.361694  
2010-01-08 MMM     66.829300

In [43]:
for stock in stocks_data:
    stock["Log"] = np.log(stock["Adj Close"])
    stock["Returns"] = stock["Log"].diff()
    stock["Returns"][0] = stock["Returns"][1]

stocks_data

C:\Users\Hugo\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


[                  High         Low        Open       Close      Volume  \
 Date                                                                     
 2010-01-04   83.449997   82.669998   83.089996   83.019997   3043700.0   
 2010-01-05   83.230003   81.699997   82.800003   82.500000   2847000.0   
 2010-01-06   84.599998   83.510002   83.879997   83.669998   5268500.0   
 2010-01-07   83.760002   82.120003   83.320000   83.730003   4470100.0   
 2010-01-08   84.320000   83.300003   83.690002   84.320000   3405800.0   
 2010-01-11   84.599998   83.410004   84.379997   83.980003   2927100.0   
 2010-01-12   84.180000   83.300003   83.580002   84.050003   3031800.0   
 2010-01-13   84.110001   83.199997   84.110001   83.779999   3102000.0   
 2010-01-14   83.930000   83.419998   83.739998   83.500000   2634100.0   
 2010-01-15   84.089996   82.870003   83.519997   83.370003   3955000.0   
 2010-01-19   85.169998   83.500000   83.820000   85.120003   4500400.0   
 2010-01-20   85.129997  

In [26]:
#Code de Landeau
def log_stock_return(data):
    # Log the prices
    data["Log"] = np.log(data["Adj Close"])
    # Compute the difference
    data["Returns"] = data.groupby(by="Ticker")["Adj Close"].diff()
    # Fill the NA values with the stock return mean 
    data["Returns"] = data.groupby(by="Ticker")["Returns"].apply(lambda x: x.fillna(x.mean()))
    return data
def compute_statistics(data):
    return data.groupby(by="Ticker")["Returns"].agg({"statistics": [np.mean, np.std,stats.skew,stats.kurtosis]})
def plot_density(data, stat):
    d=stats.gaussian_kde(data[stat])
    if stat == 'mean':
        ind = np.linspace(-0.5,0.5,500)
    elif stat == 'kurtosis':
        ind = np.linspace(-150,200,500)
    else:
        ind = np.linspace(-20,20,500)
    kdepdf = d.evaluate(ind)
    #plt.figure(figsize=(10,8))
    # plot histgram of sample
    plt.plot(ind, stats.norm.pdf(ind, loc = np.mean(data[stat]), scale = np.std(data[stat])), color="r", label='DGP normal')
    # plot estimated density
    label = '{} kde'.format(stat)
    plt.plot(ind, kdepdf, label=label, color="g")
    plt.title('Empirical {} density vs Gaussian'.format(stat))

In [28]:
# Compute the log_stock_return
return_data = log_stock_return(stocks_data)
# Create the matrix with mean, std, skewness and kurtosis
#statistics_matrix = compute_statistics(return_data)
# Drop the level "statistics"
#statistics_matrix.columns = statistics_matrix.columns.droplevel()

ValueError: 

In [8]:
dfcsv = pd.read_csv('Data/F-F_Research_Data_5_Factors_2x3_daily.csv', header=2, index_col = 0)
dfcsv

Mkt-RF   SMB   HML   RMW   CMA     RF
19630701   -0.67  0.00 -0.32 -0.01  0.15  0.012
19630702    0.79 -0.27  0.27 -0.07 -0.19  0.012
19630703    0.63 -0.17 -0.09  0.17 -0.33  0.012
19630705    0.40  0.08 -0.28  0.08 -0.33  0.012
19630708   -0.63  0.04 -0.18 -0.29  0.13  0.012
19630709    0.45  0.00  0.10  0.14 -0.04  0.012
19630710   -0.18  0.21  0.01  0.06 -0.07  0.012
19630711   -0.16  0.14 -0.30 -0.06  0.05  0.012
19630712   -0.12  0.02 -0.11  0.12  0.04  0.012
19630715   -0.62  0.07 -0.03  0.17 -0.06  0.012
19630716   -0.07 -0.08  0.14 -0.06 -0.07  0.012
19630717   -0.33 -0.07  0.15  0.04  0.10  0.012
19630718   -0.54  0.27  0.05 -0.03  0.32  0.012
19630719   -0.23 -0.06 -0.05  0.16 -0.31  0.012
19630722   -0.70 -0.11 -0.31 -0.01 -0.10  0.012
19630723    0.01 -0.10 -0.20  0.04 -0.08  0.012
19630724    0.46 -0.10 -0.01 -0.11 -0.31  0.012
19630725   -0.04  0.14  0.26 -0.16  0.18  0.012
19630726    0.35 -0.14  0.07  0.04 -0.08  0.012
19630729    0.11 -0.17  0.26  0.07 -0.11  0.012
19630730    0.84 -0.29 -0.27  0.53 -0.40  0.012
19630731   -0.13  0.11 -0.01 -0.15  0.34  0.012
19630801   -0.08 -0.12 -0.12  0.17 -0.02  0.011
19630802    0.29 -0.14  0.15 -0.05  0.02  0.011
19630805    0.57 -0.42  0.16  0.03  0.11  0.011
19630806    0.60 -0.34  0.25  0.01 -0.03  0.011
19630807   -0.19  0.04  0.17 -0.19  0.14  0.011
19630808    0.14 -0.01 -0.25  0.29 -0.33  0.011
19630809    0.60 -0.09 -0.06  0.22 -0.17  0.011
19630812    0.24  0.20  0.41 -0.13  0.32  0.011
...          ...   ...   ...   ...   ...    ...
20190215    1.13  0.38  0.53 -0.21  0.03  0.010
20190219    0.19  0.30  0.32 -0.01  0.23  0.010
20190220    0.19  0.29  0.59  0.03 -0.24  0.010
20190221   -0.37 -0.03 -0.26  0.60  0.10  0.010
20190222    0.65  0.38 -1.37  0.30 -0.62  0.010
20190225    0.15 -0.25 -0.20 -0.73 -0.53  0.010
20190226   -0.16 -0.67 -0.32  0.08 -0.17  0.010
20190227    0.09  0.16 -0.16 -0.64 -0.13  0.010
20190228   -0.31 -0.03 -0.27  0.31  0.17  0.010
20190301    0.72  0.27 -0.48 -0.33 -0.20  0.009
20190304   -0.52 -0.39  0.32  0.13 -0.07  0.009
20190305   -0.17 -0.32 -0.22  0.26 -0.03  0.009
20190306   -0.84 -1.24  0.08  0.52  0.11  0.009
20190307   -0.82 -0.05 -0.28 -0.33  0.14  0.009
20190308   -0.22  0.06 -0.13 -0.11 -0.26  0.009
20190311    1.49  0.26 -0.49 -0.29 -0.47  0.009
20190312    0.25 -0.31 -0.05 -0.42  0.00  0.009
20190313    0.68 -0.32  0.02 -0.18  0.18  0.009
20190314   -0.10 -0.39  0.26 -0.16 -0.10  0.009
20190315    0.48 -0.25 -0.28 -0.05 -0.21  0.009
20190318    0.46  0.21  0.34 -0.07 -0.06  0.009
20190319   -0.09 -0.46 -0.89  0.05 -0.09  0.009
20190320   -0.39 -0.23 -0.99 -0.15 -0.27  0.009
20190321    1.11  0.16 -1.12  0.37 -0.36  0.009
20190322   -2.17 -1.58  0.06  0.53  0.58  0.009
20190325   -0.05  0.60 -0.30  0.20  0.05  0.009
20190326    0.76  0.24  0.43  0.02  0.18  0.009
20190327   -0.50  0.16  0.51  0.74  0.11  0.009
20190328    0.40  0.37 -0.10 -0.12 -0.07  0.009
20190329    0.66 -0.29 -0.85  0.24 -0.18  0.009

[14032 rows x 6 columns]

<h2>Question1</h2>

<h2>Question2</h2>

<h2>Question3</h2>

<h2>Question4</h2>